In [1]:
using DifferentialEquations
using Plots
using LinearAlgebra
import ForwardDiff
import DiffResults
using AstrodynamicsBase
# import joptimise
using Printf
using JSON
using CSV
using DataFrames
using ColorSchemes


In [2]:
include("../../julia-r3bp/R3BP/src/R3BP.jl")
include("../src/SailorMoon.jl")   # relative path to main file of module
param3b = SailorMoon.dynamics_parameters()
paramMulti = SailorMoon.multi_shoot_parameters(param3b)
plotly()

┌ Warning: Replacing docs for `Main.SailorMoon.integrate_rk4 :: Union{Tuple{ODEProblem, Real}, Tuple{ODEProblem, Real, Union{Nothing, Vector{T} where T}}, Tuple{ODEProblem, Real, Union{Nothing, Vector{T} where T}, Bool}, Tuple{ODEProblem, Real, Union{Nothing, Vector{T} where T}, Bool, Bool}}` in module `Main.SailorMoon`
└ @ Base.Docs docs\Docs.jl:240
┌ Warning: For saving to png with the `Plotly` backend `PlotlyBase` and `PlotlyKaleido` need to be installed.
│   err =
│    ArgumentError: Package PlotlyBase not found in current path:
│    - Run `import Pkg; Pkg.add("PlotlyBase")` to install the PlotlyBase package.
│    
└ @ Plots C:\Users\yujit\.julia\packages\Plots\nuwp4\src\backends.jl:545


Plots.PlotlyBackend()

In [3]:
function plot_circle(radius, x, y, n=100)
    circle = zeros(2,n)
    thetas = LinRange(0.0, 2π, n)
    for i = 1:n
        circle[1,i] = radius*cos(thetas[i]) + x
        circle[2,i] = radius*sin(thetas[i]) + y
    end
    return circle
end


function interpolatecolor(value, vmin, vmax)
    cs = ColorSchemes.rainbow
    color = cs[(value - vmin) / (vmax - vmin)]
    return color
end

interpolatecolor (generic function with 1 method)

In [4]:
moon     = plot_circle(1-param3b.mu2, param3b.as , 0.0)
earth    = plot_circle(param3b.mu2, param3b.as, 0.0)
earth_ub = plot_circle(param3b.mu2+6375/param3b.lstar, param3b.as, 0.0)
earth_lb = plot_circle(param3b.mu2-6375/param3b.lstar, param3b.as, 0.0)
moon_soi_outer = plot_circle(1-param3b.mu2+66000/param3b.lstar, param3b.as, 0.0);

In [5]:
### PARAMETERS ###################################
# csv file to load the initial solution
filename = "../run/grid_search_Tsit5_0322.csv"
# dv_dir function corresponding to the csv file 
dir_func = SailorMoon.dv_no_thrust 

# 3body parameter
param3b = SailorMoon.dynamics_parameters()

n_arc = 5
##################################################

if dir_func == SailorMoon.dv_no_thrust
    τ_ig = 0.0
else 
    τ_ig = 1.0
end

# load initial guess
df = DataFrame(CSV.File(filename));

# maybe want to use "for row in eachrow(df)" to automate the process...? 
# row = df[1,:]



In [79]:
pcart_ = plot(
    size=(700,500), xlims=[383, 395], ylims=[-5,5], frame_style=:box, aspect_ratio=:equal, grid=0.4, legend=false, xlabel="x", ylabel="y"
);

# colors = [interpolatecolor(i, 1, nrow(df)) for i in 1:nrow(df)]
tofs = [row.tof for row in eachrow(df)]
tof_max = maximum(tofs)
tof_min = minimum(tofs)

tof_min_days = tof_min * param3b.tstar / (24*60*60)
tof_max_days = tof_max * param3b.tstar / (24*60*60)

for (i, row) in enumerate( eachrow( df ) ) 
    
    color = interpolatecolor(row.tof*param3b.tstar/(24*60*60), tof_min_days, tof_max_days)

    tof = row.tof
    rp = row.rp_kep
    ra = row.ra_kep
    α = row.alpha
    m_rp = row.m_rp

    θsf = row.thetasf
    ϕ0  = row.phi0

    x_lpo  = row.x_lpo
    y_lpo  = row.y_lpo
    z_lpo  = row.z_lpo
    vx_lpo = row.xdot_lpo
    vy_lpo = row.ydot_lpo
    vz_lpo = row.zdot_lpo

    svf = [x_lpo, y_lpo, z_lpo, vx_lpo, vy_lpo, vz_lpo, 1.0]
    tspan = [0, -tof]
    params = [
        param3b.mu2, param3b.mus, param3b.as, pi - θsf, param3b.oml, param3b.omb, 
        1.0, 0.0, 0.0, 
        paramMulti.mdot, paramMulti.tmax, dir_func, param3b.tstar
    ]
    prob = ODEProblem(SailorMoon.rhs_bcr4bp_sb1frame2_thrust_bal!, svf, tspan, params)
    sol = solve(prob, Tsit5(); reltol=1e-12, abstol=1e-12)
    
    plot!(pcart_, sol[1,:], sol[2,:], c=color)
end

# dummy plot for color bar
plot!(pcart_, [0,0], [0,1], marker_z=[15, 1], c=:rainbow, clims = (tof_min_days, tof_max_days), seriestype=:scatter, cb=:right, colorbar_title="ToF [days]")

plot!(pcart_, earth[1,:], earth[2,:], c=:green, lw=1.0, label="earth")
plot!(pcart_, earth_ub[1,:], earth_ub[2,:], c=:black, lw=1.0, label="earth")
plot!(pcart_, earth_lb[1,:], earth_lb[2,:], c=:black, lw=1.0, label="earth")
plot!(pcart_, moon[1,:], moon[2,:], c=:orange, lw=1.0, label="moon")
plot!(pcart_, moon_soi_outer[1,:], moon_soi_outer[2,:], c=:black, lw=1.0, label="moon_soi_outer")